In [8]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import string
import re
import random
import numpy as np
import pandas as pd

import pickle
import jieba
import h5py

SOS_token = 0
EOS_token = 1
class Lang:
    def __init__(self, name):
        self.name = name
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "SOS", 1: "EOS"}
        self.n_words = 2  # Count SOS and EOS

    #通过不断输入sentence（字符串的格式），构建词与下标的对应（词典），方便制作one-hot。
    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1
            
    def save(self, path):
        with open(path,'wb') as f:
            pickle.dump([self.name,self.word2index, self.word2count, self.index2word, self.n_words],f)
    
    def load(self,path):
        with open(path,'rb') as f:
            name, self.word2index, self.word2count, self.index2word, self.n_words = pickle.load(f)
        if self.name != name:
            print('error: Name error------------------------------!')
            
            
##################################################################

def unicodeToAscii(s):
    return ''.join(
        c for c in unicodedata.normalize('NFD', s)
        if unicodedata.category(c) != 'Mn'
    )
def normalizeString(s):
    s = unicodeToAscii(s.lower().strip())
    s = re.sub(r"([.!?])", r" \1", s)
    s = re.sub(r"[^a-zA-Z.!?]+", r" ", s)
    return s

def normalizeChinese(s):
    try:
        s.encode("gb2312")
    except UnicodeEncodeError:
        return ' '
    s = re.sub(r"[~!@#$%^&* ]+",r' ', s)
    return s


#lang1 = 'zh'  lang2 = 'en'
#默认英文到中文
def readTrainLangs(lang1, lang2, reverse=True,fenci = False):
    print("Reading lines...")

    zh_lines = open('../data/train.%s'% lang1).read().strip().split('\n')
    #zh_lines = zh_lines[0:20]  #for test

    zh_data_list = []
    if fenci:
        #jieba 分词
        for line in zh_lines:
            seg_line = jieba.cut(line,cut_all=False)
            #dic = [seg for seg in seg_line]
            dic = ' '.join(seg_line)
            tmp = ' '
            for char in dic.split(' '):
                val = normalizeChinese(char)
                tmp += val+' '
            zh_data_list.append(tmp)
    else: #用空格按字分开
        for line in zh_lines:
            dic = ' '.join(line)
            tmp = ' '
            for char in dic.split(' '):
                val = normalizeChinese(char)##去除生僻词
                tmp += val+' '
            zh_data_list.append(tmp)

    en_lines = open('../data/train.%s'% lang2).read().strip().split('\n')
    #en_lines = en_lines[0:20]  #for test
    
    # Split every line into pairs and normalize
    #去掉一些标点符号
    en_data_list = [[normalizeString(s) for s in l.split('\t')] for l in en_lines]
    pairs = []
    if reverse:
        input_lang = Lang(lang2)
        output_lang = Lang(lang1)
        for en,zh in zip(en_data_list,zh_data_list):
            input_lang.addSentence(en[0])
            output_lang.addSentence(zh)
            pairs.append([en[0].encode('utf-8'),zh.encode('gb2312')])
    else:
        input_lang = Lang(lang1)
        output_lang = Lang(lang2)
        for en,zh in zip(en_data_list,zh_data_list):
            input_lang.addSentence(zh)
            output_lang.addSentence(en[0])
            pairs.append([zh.encode('gb2312'), en[0].encode('utf-8')])
            
    return input_lang, output_lang, pairs
##################################################

#这部分就是对数据进行处理的函数了，上面写的函数都会在这里被调用
#最后得到三个变量input_lang，output_lang分别是源语言和目标语言的类，包含它们各自的词典。
#pairs是一个列表，列表的元素是一个二元tuple，tuple里面的内容是一句源语言字符串，一句目标语言字符串。
def prepareData(lang1, lang2, reverse=True, fenci=False):
    input_lang, output_lang, pairs = readTrainLangs(lang1, lang2, reverse, fenci)
    print("Read %s sentence pairs" % len(pairs))
    print(pairs[0][0].decode('utf-8'),pairs[0][1].decode('gb2312'))
    #pairs = filterPairs(pairs)
    #print("Trimmed to %s sentence pairs" % len(pairs))
    print("Counting words...")
#     for pair in pairs:
#         input_lang.addSentence(pair[0].decode('utf-8'))
#         output_lang.addSentence(pair[1].decode('gb2312'))
    print("Counted words:")
    print(input_lang.name, input_lang.n_words)
    print(output_lang.name, output_lang.n_words)
    return input_lang, output_lang, pairs


In [11]:
inputLang, outputLang, pairs = prepareData('zh','en')

Reading lines...
Read 9903244 sentence pairs
a pair of red crowned cranes have staked out their nesting territory  一 对 丹 顶 鹤 正 监 视 着 它 们 的 筑 巢 领 地 
Counting words...
Counted words:
en 6754
zh 388091


In [12]:
inputLang.save('../data/en_train.pkl')
outputLang.save('../data/zh_train.pkl')

h5 = h5py.File('../data/train_afterProcess.h5py','w')
h5.create_dataset('pairs',data=pairs,dtype = 'S400')
h5.close()

In [ ]:
h5py_file = h5py.File('../data/train_afterProcess.h5py','r')
pairs = h5py_file['pairs']
print(pairs[0][0].decode('utf-8'))
print(pairs[0][1].decode('gb2312'))

inputlang = dp.Lang('en')
outputlang = dp.Lang('zh')
inputlang.load('../data/en_train.pkl')
outputlang.load('../data/zh_train.pkl')

print(inputlang.name)
h5py_file.close()

In [8]:
import numpy as np
tt = ['我是中国人'.encode('gb2312'),'sdfeow dsf df dsf '.encode('utf-8')]
h5 = h5py.File('../data/test1.h5py','w')
h5.create_dataset('pairs',data=tt,dtype = 'S400')
h5.close()

In [9]:


inputlang = Lang('en')
inputlang.load('../data/en_train.pkl')

print(inputlang.word2count)


error: Name error------------------------------!
{'': 648145, 'bombabcin': 1, 'buckyball': 6, 'junichiro': 70, 'sibiu': 6, 'implemen': 1, 'externo': 1, 'finefor': 1, 'safecracking': 10, 'dietotheorapy': 1, 'peocame': 1, 'huangjianxiang': 1, 'shahekou': 1, 'parn': 2, 'illiad': 1, 'therap': 1, 'frente': 1, 'gravida': 18, 'appetence': 9, 'inhaie': 2, 'mugrabi': 1, 'quasimondo': 1, 'beclouded': 1, 'photrapher': 1, 'hearer': 33, 'petrepeter': 1, 'reviewingthe': 1, 'pyrolyzing': 1, 'gulin': 1, 'lesomiller': 2, 'inink': 1, 'strom': 18, 'eetcaferoof': 1, 'deader': 33, 'demikhovs': 1, 'macaroni': 198, 'andlocal': 2, 'chincken': 1, 'gesu': 3, 'nineth': 3, 'flyby': 23, 'xitongjiaonang': 1, 'panzergrenadiers': 1, 'whocannot': 1, 'csoma': 1, 'chemopreventive': 1, 'dashwood': 63, 'hoak': 1, 'clevon': 3, 'lidington': 2, 'rizvan': 5, 'machinet': 1, 'sepat': 6, 'englishization': 1, 'evetywhere': 1, 'elser': 3, 'instaiment': 1, 'wangcun': 1, 'randanly': 1, 'jantarova': 1, 'ziwei': 2, 'reasonableness': 4

NameError: name 'cout' is not defined

In [17]:
count = inputlang.word2count
wordFreqLess10 = 0#保存词频小于某个阈值的词
wordFreqMore100 = 0
all_word_count=0
print('input english word count:' , inputlang.n_words)
for word in count:
    all_word_count += count[word]
    if count[word] < 10:
        wordFreqLess10 +=count[word]
    if count[word] > 100:
        wordFreqMore100 +=count[word]
print('word count larger than 100:',wordFreqMore100)
print('word count Less than 10:',wordFreqLess10)
print('rate of word count less than 10:', float(wordFreqLess10)/float(all_word_count))

input english word count: 388091
word count larger than 100: 112795369
word count Less than 10: 638482
rate of word count less than 10: 0.005533974708892589


In [14]:

pairs1 = {'我':1,'人':2}
pairs2 = [1,2,3,4]
pairs3 = 90

In [22]:
pickle_file = open('../data/test.pkl','wb')
pickle.dump([pairs1,pairs2,pairs3], pickle_file)
pickle_file.close()

In [23]:
f = open('../data/test.pkl','rb')
a1,a2,a3 = pickle.load(f)
print(a1,a2,a3)


{'人': 2, '我': 1} [1, 2, 3, 4] 90


In [ ]:
import dataProcess as dp
pairs =  dp.readTrainLangs('zh','en')

Reading lines...


Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache
Dumping model to file cache /tmp/jieba.cache
Dump cache file failed.
Traceback (most recent call last):
  File "/data/liwb/anaconda3/lib/python3.5/site-packages/jieba/__init__.py", line 152, in initialize
    _replace_file(fpath, cache_file)
PermissionError: [Errno 1] Operation not permitted: '/tmp/tmpoz_v2tcn' -> '/tmp/jieba.cache'
Loading model cost 1.016 seconds.
Prefix dict has been built succesfully.


In [10]:
pickle_file = open('../data/train_pairs.pkl','rb')
pairs_pkl = pickle.load(pickle_file)

print(pairs_pkl['a'])

1


In [11]:
pairs_pkl[:10]

[[['一对', '丹顶鹤', '正', '监视', '着', '它们', '的', '筑巢', '领地'],
  'a pair of red crowned cranes have staked out their nesting territory'],
 [['一对',
   '乌鸦',
   '飞',
   '到',
   '我们',
   '屋顶',
   '上',
   '的',
   '巢里',
   '，',
   '它们',
   '好像',
   '专门',
   '为拉木',
   '而',
   '来',
   '的',
   '。'],
  'a pair of crows had come to nest on our roof as if they had come for lhamo .'],
 [['一对', '乖乖仔', '开着', '老爸', '的', '车子', '。'],
  'a couple of boys driving around in daddy s car .'],
 [['一对', '九', '？', '一对', '九', '你', '就', '全', '下注', '了', '？'],
  'a pair of nines ? you pushed in with a pair of nines ?'],
 [['一对二', '总', '不是', '好事', '，'], 'fighting two against one is never ideal '],
 [['一对二', '，', '沃克', '传给', '波顿', '。'],
  'it s a neat one two . walker to burton .'],
 [['一对二', '胜', '。'], 'deuces the winner .'],
 [['一对', '五', '。', '一对', '五', '。', '胜算', '不大', '啊', '。'],
  'five on one . five on one . yeah not the greatest odds .'],
 [['一对', '五年', '没见', '过', '的', '姐妹', '一场', '激烈', '的', '争吵', '？'],
  'an incred

### 匹配生僻字与非法字符

In [83]:
import re

def is_rare_name(string):
    pattern = re.compile(u"[~!@#$%^&* ]")
    match = pattern.search(string)
    if match:
        return True
    try:
        string.encode("gb2312")
    except UnicodeEncodeError:
        return True
    return False

def normalizeChinese(s):
    try:
        s.encode("gb2312")
    except UnicodeEncodeError:
        return ' '
    s = re.sub(r"[~!@#$%^&* ]+",r' ', s)
    return s


In [97]:
str1 = '我 是 @ 中 国 人 ， 我 # 不 才 囧 怪。'
#str1 = 'I an # a boy'
l = [normalizeChinese(s) for s in str1.split(' ')]
print(l)
tmp = ' '
for s in str1.split(' '):
    val = normalizeChinese(s)
    tmp += val+' '
print(tmp)

['我', '是', ' ', '中', '国', '人', '，', '我', ' ', '不', '才', ' ', '怪。']
 
 我 是   中 国 人 ， 我   不 才   怪。 


In [40]:
result = re.search(r'.','I love FishC.com!')
print(result.group())

I


In [91]:
s = '我 是 @ 中 国 人 ， 我 # 不 囧 才 怪。'
s = re.sub(r"[~!@#$%^&* ]+",r' ', s)
print (s)

我 是 中 国 人 ， 我 不 囧 才 怪。
